##  Air quality: design and implement your product

Welcome to the final lab of this project. Here again, you'll be working with the dataset you've now become familiar with from the air quality monitoring network in Bogotá [RMCAB](http://201.245.192.252:81/home/map). In this notebook, you will complete the following steps:

1. Import Python packages.
2. Load the dataset with missing values filled in. 
3. Add latitude and longitude to the dataset.
4. Use the nearest neighbor method to make a map of PM2.5 in Bogotá.
5. Calculate mean absolute error for different values of k using the nearest neighbor method.
6. Use the best value of k to make a map of PM2.5 in Bogotá.
7. Construct a map animation of the past 24 hours of PM2.5 in Bogotá.
8. Display your map animation


## 1. Import Python packages.

Run the next cell to import that Python packages you'll need for this lab.

In [1]:
# Import Python packages.
import os, re
import folium
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import utils
from sklearn.metrics import mean_absolute_error
from sklearn.neighbors import KNeighborsRegressor
from datetime import datetime

## 2. Load the dataset with missing values filled in (output from the last lab)

Run the next cell to read in the dataset that was the final output from the last lab, namely, a dataset with all missing values for the pollutants filled in. 

In [2]:
# Load the dataset with missing values filled in.
full_dataset = pd.read_csv('data/data_final_no_missing_PM25.csv')
full_dataset['DateTime'] = pd.to_datetime(full_dataset['DateTime'], dayfirst=True)
full_dataset

PM2.5   PM10       CO     NO2     NOX      NO  OZONO Station  \
0        32.7   56.6  0.44924  15.962  23.493   7.504  2.431     USM   
1        39.3   59.3  0.69832  17.866  34.426  16.560  1.121     USM   
2        70.8   96.4  0.88243  17.802  40.791  22.989  1.172     USM   
3        81.0  108.3  0.29549   9.886  13.591   3.704  6.565     USM   
4        56.1   87.7  0.16621   9.272  11.371   2.098  9.513     USM   
...       ...    ...      ...     ...     ...     ...    ...     ...   
166435   12.0   43.1  0.98779  23.697  35.468  11.771  8.146     KEN   
166436   35.0   35.0  0.85772  21.677  28.311   6.634  8.055     KEN   
166437   43.0   43.5  0.84339  19.867  22.533   2.666  6.877     KEN   
166438   55.0   60.1  0.84038  19.689  22.311   2.622  6.533     KEN   
166439   46.0   54.1  0.79061  17.430  19.504   2.074  6.242     KEN   

                  DateTime  
0      2021-01-01 00:00:00  
1      2021-01-01 01:00:00  
2      2021-01-01 02:00:00  
3      2021-01-01 03:00:00  
4      2021-01-01 04:00:00  
...                    ...  
166435 2021-12-31 19:00:00  
166436 2021-12-31 20:00:00  
166437 2021-12-31 21:00:00  
166438 2021-12-31 22:00:00  
166439 2021-12-31 23:00:00  

[166440 rows x 9 columns]

## 3. Add latitude and longitude to the dataset.

Run the next cell to load in a dataset with all of the sensor station locations and add that information to your original dataset. 

In [3]:
# Read in a csv file containing location data and format appropriately
stations = pd.read_csv('data/stations_loc.csv')
stations = stations[['Sigla', 'Latitud', 'Longitud']]
stations = stations.rename(columns={'Sigla': 'Station'})
stations['Latitud'] = stations['Latitud'].apply(utils.parse_dms)
stations['Longitud'] = stations['Longitud'].apply(utils.parse_dms)
# Add location data as extra columns to air pollution dataset
full_dataset = pd.merge(full_dataset, stations, on='Station', how='inner')
full_dataset.head(5)

PM2.5   PM10       CO     NO2     NOX      NO  OZONO Station  \
0   32.7   56.6  0.44924  15.962  23.493   7.504  2.431     USM   
1   39.3   59.3  0.69832  17.866  34.426  16.560  1.121     USM   
2   70.8   96.4  0.88243  17.802  40.791  22.989  1.172     USM   
3   81.0  108.3  0.29549   9.886  13.591   3.704  6.565     USM   
4   56.1   87.7  0.16621   9.272  11.371   2.098  9.513     USM   

             DateTime   Latitud   Longitud  
0 2021-01-01 00:00:00  4.532097 -74.116947  
1 2021-01-01 01:00:00  4.532097 -74.116947  
2 2021-01-01 02:00:00  4.532097 -74.116947  
3 2021-01-01 03:00:00  4.532097 -74.116947  
4 2021-01-01 04:00:00  4.532097 -74.116947

## 4. Use the nearest neighbor method with k=1 to make a map of PM2.5 in Bogotá.

In [4]:
# Define a value for k
k = 1
neighbors_model = KNeighborsRegressor(n_neighbors=k, weights = 'distance', metric='sqeuclidean')
# Isolate a single time step from the dataset
time_step = datetime.fromisoformat('2021-08-04T08:00:00')
time_step_data = full_dataset[full_dataset['DateTime'] == time_step]
neighbors_model.fit(time_step_data[['Latitud', 'Longitud']], time_step_data[["PM2.5"]])
time_step_data

PM2.5   PM10       CO     NO2     NOX      NO   OZONO Station  \
5168     22.3   39.4  0.44301  10.054  20.201  10.148  17.765     USM   
13928    23.2   64.5  0.69052  27.013  42.279  15.266   6.658     BOL   
22688    25.0   41.7  0.70600  17.195  27.279  10.084  14.059     SUB   
31448     6.0   27.0  0.60225   6.320   9.603   3.285  22.296     TUN   
40208    37.0   37.3  1.64300  36.610  70.158  33.484  10.142     LFR   
48968    34.0   37.4  0.60224  16.703  29.447  12.795  17.152     PTE   
57728    30.0    NaN  1.08365     NaN     NaN     NaN  11.133     MAM   
66488    28.2   47.3  0.34007   5.813   8.266   2.452  16.332     CBV   
75248    37.0   53.3  0.71508  17.363  30.222  12.859  17.362    CDAR   
84008    16.0   18.0  0.62339  14.718  29.180  14.462  15.301     SCR   
92768    30.0   59.9  0.57825  15.847  24.559   8.727  22.096     FTB   
101528   19.8   38.2  0.41351  11.546  19.227   7.681  22.577     JAZ   
110288   32.3   50.3      NaN     NaN     NaN     NaN     NaN     7MA   
119048   39.0  109.0  1.66859     NaN     NaN     NaN  13.124     CSE   
127808   32.0   52.0  0.20459  18.453  30.221  11.769  17.775     GYR   
136568    7.3   39.1  0.77527  36.312  55.231  18.919   8.020     COL   
145328   22.7   52.2      NaN  22.505  49.354  26.849  19.865    MOV2   
154088    8.0   25.5  1.12750  27.371  61.969  34.598  12.363     USQ   
162848   21.0  120.2      NaN  18.635  37.899  19.264  19.992     KEN   

                  DateTime   Latitud   Longitud  
5168   2021-08-04 08:00:00  4.532097 -74.116947  
13928  2021-08-04 08:00:00  4.735578 -74.125925  
22688  2021-08-04 08:00:00  4.761222 -74.093433  
31448  2021-08-04 08:00:00  4.576206 -74.130975  
40208  2021-08-04 08:00:00  4.690628 -74.082378  
48968  2021-08-04 08:00:00  4.631817 -74.117278  
57728  2021-08-04 08:00:00  4.625364 -74.066972  
66488  2021-08-04 08:00:00  4.577889 -74.166272  
75248  2021-08-04 08:00:00  4.658417 -74.083944  
84008  2021-08-04 08:00:00  4.572558 -74.083639  
92768  2021-08-04 08:00:00  4.678169 -74.143714  
101528 2021-08-04 08:00:00  4.608417 -74.114869  
110288 2021-08-04 08:00:00  4.645117 -74.061503  
119048 2021-08-04 08:00:00  4.595958 -74.148483  
127808 2021-08-04 08:00:00  4.783614 -74.043994  
136568 2021-08-04 08:00:00  4.736981 -74.069472  
145328 2021-08-04 08:00:00  4.667789 -74.148483  
154088 2021-08-04 08:00:00  4.710381 -74.030414  
162848 2021-08-04 08:00:00  4.625083 -74.161222

In [5]:
# Generate a map of predictions for Bogotá
predictions_xy, dlat, dlon = utils.predict_on_bogota(neighbors_model, 64)
utils.create_heat_map(predictions_xy, time_step_data, dlat, dlon)

## 5. Test different values of k for the nearest neighbor method.
Run the cell below to calculate the mean absolute error for k=1, or in other words, the error associated with using just one nearest neighbor as you did to create the map above. The calculation for mean absolute error that's being performed by the code before is the following:

$$MAE = \frac{1}{n} \sum_{i=1}^{n}{|\rm{actual}_i - \rm{model}_i|}$$
    
Where "n" is the number of samples in the test dataset

After testing k=1, run the following cell to test a range of values for k.

In [6]:
# Make an estimate of mean absolute error for k=1 by testing the method on 10% of the full dataset
utils.calculate_mae_for_k(full_dataset, k=1)

7.755365195301528

In [7]:
# Make an estimate of mean absolute error for a range of k values.
kmin = 1
kmax = 9
for kneighbors in range(kmin, kmax+1):
    print(f'k = {kneighbors}, MAE = {utils.calculate_mae_for_k(full_dataset, k=kneighbors)}')

k = 1, MAE = 7.755365195301528
k = 2, MAE = 7.121303933642593
k = 3, MAE = 6.982897094122495
k = 4, MAE = 6.946129095997671
k = 5, MAE = 6.934877267030211
k = 6, MAE = 6.9312845003464885
k = 7, MAE = 6.929711326789344
k = 8, MAE = 6.928685015704663
k = 9, MAE = 6.927768921775057


## 6. Use the best value of k to make a map of PM2.5 in Bogotá.

Run the cell below to generate a map PM2.5 values averaged over the time period from `start_date` to `end_date`. You can change the value of `k` to see how the result changes depending on `k`.

In [9]:
k = 1
start_date = datetime.fromisoformat('2021-08-04T08:00:00')
end_date = datetime.fromisoformat('2021-08-05T08:00:00')

utils.create_heat_map_with_date_range(full_dataset, start_date, end_date, k_neighbors=k)

<Figure size 432x288 with 0 Axes>

## 7. Construct a map animation of the past 24 hours of PM2.5 in Bogotá.
Run the next cell to generate an animation of the past 24 hours. You can change k to use a different number of neighbors and change the dates to look at a different day. 

In [10]:
# Lets make an animation on a give set of dates
k = 1
grid_density = 32
# Filter a date range
start_date = datetime.fromisoformat('2021-08-04T08:00:00')
end_date = datetime.fromisoformat('2021-08-05T08:00:00')

# Build your animation
neigh = KNeighborsRegressor(n_neighbors=k, weights = 'distance', metric='sqeuclidean')
df_days = full_dataset[full_dataset['DateTime'] >= start_date]
df_days = df_days[df_days['DateTime'] <= end_date]
unique_dates = df_days['DateTime'].unique()
df_days = df_days[['DateTime', 'Station', 'Latitud', 'Longitud', 'PM2.5']]
features = []

for day_hour in unique_dates:
    df_day = full_dataset[full_dataset['DateTime'] == day_hour]
    day_hour = str(day_hour)[0:19]
    neigh.fit(df_day[['Latitud', 'Longitud']], df_day[["PM2.5"]])
    predictions_xy, dlat, dlon = utils.predict_on_bogota(neigh, grid_density)
    for row in predictions_xy:
        rect = utils.create_pol(row, dlat, dlon, day_hour)
        #print(rect)
        features.append(rect)
print('animation created successfully! run the next cell to see the result')

animation created successfully! run the next cell to see the result


## 8. Display your map animation

Run the next cell to display the animation you created!

In [11]:
map_animation = folium.Map(location=[4.7110, -74.0721], zoom_start = 11) 

folium.plugins.TimestampedGeoJson(
    {
        "type": "FeatureCollection",
        "features": features,
    },
    period="PT1H",
    duration='PT1H',
    add_last_point=True
).add_to(map_animation)


fg = folium.FeatureGroup(name="Stations")
for index, station in df_days[df_days['DateTime'] == start_date].iterrows():
    fg.add_child(folium.CircleMarker(location=[station['Latitud'], station['Longitud']], radius = 10,
                                     fill_color=utils.color_producer(station['PM2.5'], linear=True),
                                     color = '', 
                                     fill_opacity=0.9))
    map_animation.add_child(fg)

map_animation